In [3]:
import json
import numpy as np
from ase.lattice.cubic import FaceCenteredCubic, SimpleCubic, BodyCenteredCubic
from ase.lattice.hexagonal import HexagonalClosedPacked
from ase.cluster.icosahedron import Icosahedron
from ase.cluster.decahedron import Decahedron
from ase.cluster.octahedron import Octahedron
from debyecalculator import DebyeCalculator
import torch
import plotly.graph_objects as go

def load_dict(file_name):
    with open(file_name, 'r') as f:
        return json.load(f)
    
def get_best_structure_details(result_simulated_Gr, num_best_fits=5, print_best=True):
    """
    Returns the best fits based on the rwp value.

    Parameters:
    result_simulated_Gr (list): The results to sort and print.
    num_best_fits (int): The number of best fits to print. Default is 5.
    print_best (bool): Whether or not to print the best fits. Default is True.
    """
    # Sort the results based on the rwp value
    sorted_results = sorted(result_simulated_Gr, key=lambda x: x['rwp'])

    # Get the best total structures
    best_total_structures = sorted_results[:num_best_fits]

    if print_best:
        print("\nBest total structures across all types:")
        for structure in best_total_structures:
            print(f"Structure Type: {structure['structure_type']}, Details: {structure}")
        print ()

    # Extract the structure_type, noshell, and lattice constant of the best structures
    best_structure_details = []
    for structure in best_total_structures:
        details = {
            'pH': structure['pH'],
            'pressure': structure['pressure'],
            'solvent': structure['solvent']
        }
        best_structure_details.append(details)

    # Prepare the data for use with generate_and_evaluate_clusters
    structure_types = [details['pH'] for details in best_structure_details]
    lc_list = [details['pressure'] for details in best_structure_details]
    noshells = [details['solvent'] for details in best_structure_details]

    return structure_types, lc_list, noshells

def LoadData(simulated_or_experimental='simulated', scatteringfunction='Gr'):
    # Set the filename based on the simulated_or_experimental and scatteringfunction variables
    if scatteringfunction == 'Gr':
        if simulated_or_experimental == 'simulated':
            filename = '../Data/Gr/Target_PDF_benchmark.npy'
        else:  # simulated_or_experimental == 'experimental'
            filename = '../Data/Gr/Experimental_PDF.gr'
    else:  # scatteringfunction == 'Sq'
        if simulated_or_experimental == 'simulated':
            filename = '../Data/Sq/Target_Sq_benchmark.npy'
        else:  # simulated_or_experimental == 'experimental'
            filename = '../Data/Sq/Experimental_Sq.sq'

    data = np.loadtxt(filename, skiprows=25) if filename.endswith('.gr') or filename.endswith('.sq') else np.load(filename)
    x_target = data[:, 0]
    Int_target = data[:, 1]

    return x_target, Int_target

def calculate_scattering(cluster, scatteringfunction='Gr'):
    """
    Calculate a Pair Distribution Function (PDF) or Structure Factor (Sq) from a given structure.

    Parameters:
    cluster (ase.Atoms): The atomic structure (from ASE Atoms object) to calculate the PDF or Sq from.
    scatteringfunction (str): The scatteringfunction to calculate. 'Gr' for pair distribution function, 'Sq' for structure factor. Default is 'Gr'.

    Returns:
    r/q (numpy.ndarray): The r values (for PDF) or q values (for Sq) from the calculated function.
    G/S (numpy.ndarray): The G values (for PDF) or S values (for Sq) from the calculated function.

    Raises:
    AssertionError: If the scatteringfunction parameter is not 'Gr' or 'Sq'.

    Example:
    >>> cluster = Icosahedron('Au', noshells=7)
    >>> r, G = calculate_scattering(cluster, scatteringfunction='Gr')
    >>> q, S = calculate_scattering(cluster, scatteringfunction='Sq')
    """
    # Check if the scatteringfunction parameter is valid
    assert scatteringfunction in ['Gr', 'Sq'], "scatteringfunction must be 'Gr' or 'Sq'"

    # Initialise calculator object
    calc = DebyeCalculator(qmin=2, qmax=10.0, rmax=30, qstep=0.01)

    # Extract atomic symbols and positions
    symbols = cluster.get_chemical_symbols()
    positions = cluster.get_positions()

    # Convert positions to a torch tensor
    positions_tensor = torch.tensor(positions)

    # Create a structure tuple
    structure_tuple = (symbols, positions_tensor)

    # Calculate Pair Distribution Function or Structure Factor
    if scatteringfunction == 'Gr':
        r, G = calc.gr(structure_source=structure_tuple)
        G /= G.max()
        return r, G
    else:  # scatteringfunction == 'Sq'
        q, S = calc.sq(structure_source=structure_tuple)
        S /= S.max()
        return q, S
    
def generate_and_evaluate_clusters(cluster, x_target, Int_target, scatteringfunction, plot=False):
    
    print ("Calculating scattering pattern for the following structure:")
    # Calculate the scattering pattern of the generated structure
    x_sim, Int_sim = calculate_scattering(cluster, scatteringfunction)
    print ("done")
    
    # Interpolate the simulated intensity to the r/q values of the target scattering pattern
    Int_sim_interp = np.interp(x_target, x_sim, Int_sim)

    # Calculate the difference between the simulated and target scattering patterns
    diff = Int_target - Int_sim_interp

    # Calculate the Rwp value
    rwp = np.sqrt(np.sum(diff**2) / np.sum(Int_target**2))

    # If plot is True, generate an interactive plot of the target and simulated scattering patterns
    if plot:
        fig = go.Figure()
        fig.add_trace(go.Scatter(x=x_target, y=Int_target, mode='lines', name=f'Target {scatteringfunction}', line=dict(width=4)))  # Changed name based on scatteringfunction
        fig.add_trace(go.Scatter(x=x_target, y=Int_sim_interp, mode='lines', name=f'Simulated {scatteringfunction}'))  # Changed name based on scatteringfunction
        fig.update_layout(
            title=f"Structure Type: {structure_type}, No. of Shells: {noshell}, Lattice Constant: {lc:.2f}, Rwp Value: {rwp:.2f}",
            xaxis_title="r (Å)" if scatteringfunction == 'Gr' else "q (Å^-1)",
            yaxis_title="Intensity (a.u.)",
            legend_title="Legend"
        )
        fig.show()

    return rwp

def generate_structure(pH, pressure, solvent, atom='Au'):
    """
    Generate a structure based on the given parameters.

    Parameters:
    pH (float): The pH value, which scales the size of the structure. Range: [0, 14]
    pressure (float): The pressure value, which controls the lattice constant. Range: [0, 100]
    solvent (str): The solvent type, which determines the structure type for small clusters. 
                   'Ethanol', 'Methanol', 'Water', or any other solvent
    atom (str): The atom type. Default is 'Au'.

    Returns:
    cluster: The generated structure.
    """
    # Scale the size of the structure based on pH
    scale_factor = pH / 14  # Normalize pH to range [0, 1]
    noshells = int(scale_factor * 8) + 2  # Scale noshells from 1 to 4
    p = q = r = noshells  # Set p, q, r to noshells
    layers = [noshells] * 3  # Set layers to [noshells, noshells, noshells]
    surfaces=[[1,0,0], [1,1,0], [1,1,1]]  # Set surfaces to [100], [110], [111]

    # Control lattice constant by pressure
    lc = 2 * (pressure / 100) + 2.5  # Scale lattice constant from 2.5 to 4.5 based on pressure

    # Determine the structure type based on the number of atoms and solvent
    num_atoms = noshells ** 3  # Assume the number of atoms is proportional to noshells^3
    if num_atoms > 2000: # approximate 3 nm in diameter
        if solvent == 'Ethanol':
            cluster = FaceCenteredCubic(atom, directions=surfaces, size=layers, latticeconstant=2*np.sqrt(0.5*lc**2))
            cluster.structure_type = 'FaceCenteredCubic'
        elif solvent == 'Methanol':
            cluster = SimpleCubic(atom, directions=surfaces, size=layers, latticeconstant=lc)
            cluster.structure_type = 'SimpleCubic'
        elif solvent == 'Water':
            cluster = BodyCenteredCubic(atom, directions=surfaces, size=layers, latticeconstant=lc)
            cluster.structure_type = 'BodyCenteredCubic'
        else:
            cluster = HexagonalClosedPacked(atom, latticeconstant=(lc, lc*1.633), size=(noshells, noshells, noshells))
            cluster.structure_type = 'HexagonalClosedPacked'
    elif solvent == 'Ethanol':
        cluster = Icosahedron(atom, noshells, 2*np.sqrt(0.5*lc**2))
        cluster.structure_type = 'Icosahedron'
    elif solvent == 'Methanol':
        cluster = Decahedron(atom, p, q, r, 2*np.sqrt(0.5*lc**2))
        cluster.structure_type = 'Decahedron'
    elif solvent == 'Water':
        cluster = BodyCenteredCubic(atom, directions=surfaces, size=layers, latticeconstant=lc)
        cluster.structure_type = 'BodyCenteredCubic'
    else:
        cluster = Octahedron(atom, length=noshells, latticeconstant=2*np.sqrt(0.5*lc**2))
        cluster.structure_type = 'Octahedron'

    #print("generated structure: ", cluster.structure_type)
    #print("noshells: ", noshells)
    #print ("lc: ", lc)

    return cluster,  cluster.structure_type, noshells, lc

# Results for simulated Gr data

In [4]:
# Load the results from the brute force search
result_simulated_Gr = load_dict('../results/bruteforce/result_simulated_Gr_SynthesisSpace.json')

# Load the target PDF data
x_target, Int_target = LoadData(simulated_or_experimental='simulated', scatteringfunction='Gr')

# Get the best structure details
pH, pressure, solvent = get_best_structure_details(result_simulated_Gr, num_best_fits=5, print_best=True)
atom = 'Au'
surfaces = [[1, 0, 0], [1, 1, 0], [1, 1, 1]] # Define the surfaces of the cluster
scatteringfunction = 'Gr'

# Loop through the best structures and calculate the Rwp value for each one
for i, (pH, pressure, solvent) in enumerate(zip(pH, pressure, solvent), 1):
    cluster, structure_type, noshell, lc = generate_structure(pH, pressure, solvent, atom='Au')
    print(f"The {i}{'st' if i == 1 else 'nd' if i == 2 else 'rd' if i == 3 else 'th'} best fitting structure is {structure_type} with {noshell} shells and lattice constant {lc}.")    
    rwp = generate_and_evaluate_clusters(cluster, x_target, Int_target, scatteringfunction, plot=True)



Best total structures across all types:
Structure Type: Icosahedron, Details: {'pH': 9.0, 'pressure': 16.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 923, 'rwp': 0.015542706935371858}
Structure Type: Icosahedron, Details: {'pH': 10.5, 'pressure': 16.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 1415, 'rwp': 0.09674141614834637}
Structure Type: Icosahedron, Details: {'pH': 9.0, 'pressure': 16.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 923, 'rwp': 0.09872666976386778}
Structure Type: Icosahedron, Details: {'pH': 7.0, 'pressure': 16.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 561, 'rwp': 0.1276662682339128}
Structure Type: Icosahedron, Details: {'pH': 9.0, 'pressure': 15.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 923, 'rwp': 0.12958408164690877}

The 1st best fitting structure is Icosahedron with 7 shells and lattice constant 

/var/folders/pg/s9x5c7555vb2c5gjlpnlzqyh0000gp/T/ipykernel_34385/4022398090.py:97: UserWarning:




done


The 2nd best fitting structure is Icosahedron with 8 shells and lattice constant 2.82.
Calculating scattering pattern for the following structure:
done


The 3rd best fitting structure is Icosahedron with 7 shells and lattice constant 2.83.
Calculating scattering pattern for the following structure:
done


The 4th best fitting structure is Icosahedron with 6 shells and lattice constant 2.82.
Calculating scattering pattern for the following structure:
done


The 5th best fitting structure is Icosahedron with 7 shells and lattice constant 2.81.
Calculating scattering pattern for the following structure:
done


# Results for simulated Sq data

In [10]:
# Load the results from the brute force search
result_simulated_Sq = load_dict('../results/bruteforce/result_simulated_Sq_SynthesisSpace.json')

# Load the target PDF data
x_target, Int_target = LoadData(simulated_or_experimental='simulated', scatteringfunction='Sq')

# Get the best structure details
pH, pressure, solvent = get_best_structure_details(result_simulated_Sq, num_best_fits=5, print_best=True)
atom = 'Au'
surfaces = [[1, 0, 0], [1, 1, 0], [1, 1, 1]] # Define the surfaces of the cluster
scatteringfunction = 'Sq'

# Loop through the best structures and calculate the Rwp value for each one
for i, (pH, pressure, solvent) in enumerate(zip(pH, pressure, solvent), 1):
    cluster, structure_type, noshell, lc = generate_structure(pH, pressure, solvent, atom='Au')
    print(f"The {i}{'st' if i == 1 else 'nd' if i == 2 else 'rd' if i == 3 else 'th'} best fitting structure is {structure_type} with {noshell} shells and lattice constant {lc}.")    
    rwp = generate_and_evaluate_clusters(cluster, x_target, Int_target, scatteringfunction, plot=True)


Best total structures across all types:
Structure Type: Icosahedron, Details: {'pH': 9.0, 'pressure': 16.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 923, 'rwp': 0.012020302474612329}
Structure Type: Icosahedron, Details: {'pH': 9.0, 'pressure': 16.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 923, 'rwp': 0.07627005955940168}
Structure Type: Icosahedron, Details: {'pH': 9.0, 'pressure': 15.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 923, 'rwp': 0.10041197905552111}
Structure Type: Icosahedron, Details: {'pH': 7.0, 'pressure': 16.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 561, 'rwp': 0.1261719632990958}
Structure Type: Icosahedron, Details: {'pH': 10.5, 'pressure': 16.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 1415, 'rwp': 0.12834274589665462}

The 1st best fitting structure is Icosahedron with 7 shells and lattice constant 

/var/folders/pg/s9x5c7555vb2c5gjlpnlzqyh0000gp/T/ipykernel_34385/4022398090.py:97: UserWarning:




done


The 2nd best fitting structure is Icosahedron with 7 shells and lattice constant 2.83.
Calculating scattering pattern for the following structure:
done


The 3rd best fitting structure is Icosahedron with 7 shells and lattice constant 2.81.
Calculating scattering pattern for the following structure:
done


The 4th best fitting structure is Icosahedron with 6 shells and lattice constant 2.83.
Calculating scattering pattern for the following structure:
done


The 5th best fitting structure is Icosahedron with 8 shells and lattice constant 2.82.
Calculating scattering pattern for the following structure:
done


# Results for experimental Gr data

In [11]:
# Load the results from the brute force search
result_experimental_Gr = load_dict('../results/bruteforce/result_experimental_Gr_SynthesisSpace.json')

# Load the target PDF data
x_target, Int_target = LoadData(simulated_or_experimental='experimental', scatteringfunction='Gr')

# Get the best structure details
pH, pressure, solvent = get_best_structure_details(result_experimental_Gr, num_best_fits=5, print_best=True)
atom = 'Au'
surfaces = [[1, 0, 0], [1, 1, 0], [1, 1, 1]] # Define the surfaces of the cluster
scatteringfunction = 'Gr'

# Loop through the best structures and calculate the Rwp value for each one
for i, (pH, pressure, solvent) in enumerate(zip(pH, pressure, solvent), 1):
    cluster, structure_type, noshell, lc = generate_structure(pH, pressure, solvent, atom='Au')
    print(f"The {i}{'st' if i == 1 else 'nd' if i == 2 else 'rd' if i == 3 else 'th'} best fitting structure is {structure_type} with {noshell} shells and lattice constant {lc}.")    
    rwp = generate_and_evaluate_clusters(cluster, x_target, Int_target, scatteringfunction, plot=True)


Best total structures across all types:
Structure Type: Icosahedron, Details: {'pH': 0.0, 'pressure': 18.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 13, 'rwp': 0.7822161184122359}
Structure Type: Icosahedron, Details: {'pH': 0.0, 'pressure': 19.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 13, 'rwp': 0.7827688988358288}
Structure Type: Icosahedron, Details: {'pH': 0.0, 'pressure': 18.0, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 13, 'rwp': 0.7838695242062886}
Structure Type: Icosahedron, Details: {'pH': 0.0, 'pressure': 19.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 13, 'rwp': 0.785490903293917}
Structure Type: Icosahedron, Details: {'pH': 0.0, 'pressure': 17.5, 'solvent': 'Ethanol', 'structure_type': 'Icosahedron', 'number_of_atoms': 13, 'rwp': 0.7877117250027271}

The 1st best fitting structure is Icosahedron with 2 shells and lattice constant 2.87.
Calcula

/var/folders/pg/s9x5c7555vb2c5gjlpnlzqyh0000gp/T/ipykernel_34385/4022398090.py:97: UserWarning:




The 2nd best fitting structure is Icosahedron with 2 shells and lattice constant 2.88.
Calculating scattering pattern for the following structure:
done


The 3rd best fitting structure is Icosahedron with 2 shells and lattice constant 2.86.
Calculating scattering pattern for the following structure:
done


The 4th best fitting structure is Icosahedron with 2 shells and lattice constant 2.89.
Calculating scattering pattern for the following structure:
done


The 5th best fitting structure is Icosahedron with 2 shells and lattice constant 2.85.
Calculating scattering pattern for the following structure:
done


# Results for experimental Sq data

In [27]:
# Load the results from the brute force search
result_experimental_Sq = load_dict('../results/bruteforce/result_experimental_Sq_SynthesisSpace.json')

# Load the target PDF data
x_target, Int_target = LoadData(simulated_or_experimental='experimental', scatteringfunction='Sq')

# Get the best structure details
pH, pressure, solvent = get_best_structure_details(result_experimental_Sq, num_best_fits=5, print_best=True)
atom = 'Au'
surfaces = [[1, 0, 0], [1, 1, 0], [1, 1, 1]] # Define the surfaces of the cluster
scatteringfunction = 'Sq'

# Loop through the best structures and calculate the Rwp value for each one
for i, (pH, pressure, solvent) in enumerate(zip(pH, pressure, solvent), 1):
    cluster, structure_type, noshell, lc = generate_structure(pH, pressure, solvent, atom='Au')
    print(f"The {i}{'st' if i == 1 else 'nd' if i == 2 else 'rd' if i == 3 else 'th'} best fitting structure is {structure_type} with {noshell} shells and lattice constant {lc}.")    
    rwp = generate_and_evaluate_clusters(cluster, x_target, Int_target, scatteringfunction, plot=True)


Best total structures across all types:
Structure Type: Decahedron, Details: {'pH': 12.5, 'pressure': 18.5, 'solvent': 'Methanol', 'structure_type': 'Decahedron', 'number_of_atoms': 25790, 'rwp': 0.7880204643245384}
Structure Type: Decahedron, Details: {'pH': 12.5, 'pressure': 19.0, 'solvent': 'Methanol', 'structure_type': 'Decahedron', 'number_of_atoms': 25790, 'rwp': 0.8051100687725472}
Structure Type: Decahedron, Details: {'pH': 12.5, 'pressure': 18.0, 'solvent': 'Methanol', 'structure_type': 'Decahedron', 'number_of_atoms': 25790, 'rwp': 0.8079175192573451}
Structure Type: Decahedron, Details: {'pH': 10.5, 'pressure': 18.5, 'solvent': 'Methanol', 'structure_type': 'Decahedron', 'number_of_atoms': 17931, 'rwp': 0.8170224906536757}
Structure Type: Decahedron, Details: {'pH': 10.5, 'pressure': 19.0, 'solvent': 'Methanol', 'structure_type': 'Decahedron', 'number_of_atoms': 17931, 'rwp': 0.8321716175847221}

The 1st best fitting structure is Decahedron with 9 shells and lattice constan

/var/folders/pg/s9x5c7555vb2c5gjlpnlzqyh0000gp/T/ipykernel_34385/4022398090.py:97: UserWarning:




done


The 2nd best fitting structure is Decahedron with 9 shells and lattice constant 2.88.
Calculating scattering pattern for the following structure:
done


The 3rd best fitting structure is Decahedron with 9 shells and lattice constant 2.86.
Calculating scattering pattern for the following structure:
done


The 4th best fitting structure is Decahedron with 8 shells and lattice constant 2.87.
Calculating scattering pattern for the following structure:
done


The 5th best fitting structure is Decahedron with 8 shells and lattice constant 2.88.
Calculating scattering pattern for the following structure:
done
